# Swarm Simulator for Outer Space

This swarm simulator will explore different swarm algorithms for an application in outer space. This approach will divide a plot into grid squares, which can then be analysed to determine and control the behaviour of each individual agent in the swarm.

In [1]:
#imports
import sympy as sym
import plotly as py
import plotly.tools as tls
from plotly import graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
from IPython.display import Image

import dash
from dash.dependencies import Output, Input
import dash_core_components as dcc
import dash_html_components as html

import numpy as np
import pandas as pd
import ipywidgets as widgets
import time
import math

from scipy import special
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
from collections import deque
from scipy.spatial.distance import cdist, pdist, euclidean
from sympy import sin, cos, symbols, lambdify

from robot import Robot
from dust_devil import DustDevil
from live_functions import initialise,random_position, grid_center,positions,bounce,magnitude,unit,division_check,physics_walk,dust_check,update_timestep,cluster_function,G_transition,dist,random_walk,dust,trajectory_dust,update_dust,load_positions,pre_initialise

import random
import datetime
import os
import math
import sys

import Processing_Functions_BP


import dash
from dash.dependencies import Output, Input
import dash_core_components as dcc
import dash_html_components as html

import json
import pickle

from ast import literal_eval

app = dash.Dash(__name__)

In [2]:
#Plotly offline mode
init_notebook_mode(connected=True)

## Initialisation of Constants

In [3]:
#initialising parameters
conversion_ms = 1/3.6 #km/h to m/s conversion actor
timer = 0


#Robot Parameters
robot_number = 200
robot_speed = 2 #m/s
robot_radius = 1 
robot_mass = 20 #kg
x_robot = []
y_robot = []
min_neighbour = []
gen_random = 0 #the random angle

#dust devil parameters
dust_time = 170 #time in seconds the dust devil will survive 
dust_speed = 5 #m/s
dust_radius = 6
dust_devils = []
detection = 12

#Area Parameters
area = 2 #area in km^2 
side = 1 #each side length in m
per_square_km = 100/(60*60*24)
probability_dust = per_square_km*4#(per_square_km*area) #number of dust devils per second

## Physics Constants

In [4]:
#setting physics constants
power = 2
R = 200
max_force = 1
multiply = 1.5

In [5]:
"""
#G_array = [1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000]
#power_array = [2,3,4,5]
#R_array = [10,50,100,125,150,200,250]
#multiply_array = [1,1.1,1.2,1.3,1.4,1.5,2]
robot_number_array =[100]#[10,20,30,40,50,60,70,80,90,100]#[10,25,50,100]
#initial_array = [1,10,20,30,40,50,60,70,80,90,100]
max_force = 1
seed_setup = 10

#setting timestep parameter
time = 2000
timestep_array = 1
timestep = 1
performance_metric = []
current_directory = "Experiments/Random Seed Deployment 2/"
try:
    os.mkdir(current_directory)
except OSError:
    print ("Failure: Directory creation of %s failed" % current_directory)
else:
    print ("Success: Directory creation of %s succeeded" % current_directory)


values = []
random_generated = []
for i in range(seed_setup):
    random_seed = os.urandom(8)
    
    random_generated.append(random_seed)
    for robot in robot_number_array:
        code = str(i)
        path = (current_directory + code + "/")
        try:
            os.mkdir(path)
        except OSError:
            print ("Failure: Directory creation of %s failed" % path)
        else:
            print ("Success: Directory creation of %s succeeded" % path)
        image = (current_directory + "Images/")
        try:
            os.mkdir(image)
        except OSError:
            print ("Failure: Directory creation of %s failed" % image)
        else:
            print ("Success: Directory creation of %s succeeded" % image)
        G_state = G_transition(max_force,R,power)
        #G_array = (np.arange(G_state*0.8, G_state*1.2, 0.02*G_state))
        G_array = list([G_state])
        #for in initial_array:
        for i in range(len(G_array)):
            #only set seed if eliminating bias
            #random_seed = os.urandom(8)
            #random.seed(random_seed)
            swarm = initialise(robot, side, 20)
            store_robots = np.zeros((2,robot,(time*timestep)))
            store_dust = np.zeros((2,robot,(time*timestep)))
            min_neighbours = []
            cluster_average = []
            store_dust = []
            dust_devils = []
            measurement_events = 0
            detection_metric = 0
            dust_count = 0 
            total_detection = []
            total_collision = []
            total_dust = []
            density = density_measure(robot,100,2)
            for j in range(0,time*timestep):
                #updating robots and storing
                print(j)

                store_robots[:,:,j] = positions(swarm)
                measurement_events_change,detection_metric_change = physics_walk(swarm,G_state,power,R,max_force,multiply,min_neighbours,cluster_average,detection,timestep,dust_devils)

                measurement_events = measurement_events + measurement_events_change
                detection_metric = detection_metric + detection_metric_change
                total_detection.append(detection_metric)
                total_collision.append(measurement_events)
                store_dust.append(positions(dust_devils))
                update_dust(dust_devils,dust_speed)
                if(j%timestep==0):

                    dust_count = dust_count + dust(dust_devils,1,side,j,dust_speed,1/timestep)
                total_dust.append(dust_count)


            print(total_dust)
        print(total_detection)

        print(detection_metric)
        np.save(path + "Robots.npy",store_robots)
        with open( path + "dust.txt", "w") as f:
            json.dump(store_dust, f)
        np.save(path + "Minimum Distance to Neighbours.npy",np.array(min_neighbours))
        np.save(path + "Cluster Average.npy", np.array(cluster_average))
        #np.save(path + "Measurement Events Count.npy", np.array(cluster_average))
        print("Robots: ",store_robots.shape)
        print("Dust Devils: ",len(store_dust))
        values.append([len(swarm),timestep    
                    ,G_state,power,R,multiply,max_force,robot_speed,min_neighbours[time*timestep-1],cluster_average[time*timestep-1],density,random_seed, G_state,measurement_events])
        values_title = ['Number of Robots',
                                        'Timestep',
                                        'G', 
                                        'Power', 
                                        'Communication Range', 
                                        'Multiplier',
                                        'Max Force',
                                        'Max Speed',
                                        'Minimum Distance to Neighbours',
                                        'Average Cluster Size',
                                        'Density',
                                        'Seed',
                                        'G Transition',
                                        'Measurement Events Count',
                ]
        data = {'Values':[len(swarm),G_state,power,R,multiply,max_force,robot_speed,density,random_seed, G_state]}
        titles =['Number of Robots',
                                        'G', 
                                        'Power', 
                                        'Communication Range', 
                                        'Multiplier',
                                        'Max Force',
                                        'Max Speed',
                                        'Density',
                                        'Seed',
                                        'G Transition',
                ]

        constants = pd.DataFrame(data, index = titles
                                       ) 
        print(constants.loc["Density"])
        print(constants)
        constants.to_excel(path + "Constants.xlsx")

        graph_start_path = image + code + "- Graph_Beginning.png"
        table_start_path = image + "/" + code + "- Table_Beginning.png"

        graph_start = Processing_Functions_BP.graph_figure(store_robots,0,timestep,code)
        graph_start.write_image(graph_start_path)
        table_start = Processing_Functions_BP.table_figure(store_robots,0,timestep,constants,min_neighbours,cluster_average)
        table_start.write_image(table_start_path)

        Processing_Functions_BP.combine(graph_start_path,table_start_path)

        graph_end_path = image + code + "- Graph_End.png"
        table_end_path = image + "/" + code + "- Table_End.png"

        graph_end = Processing_Functions_BP.graph_figure(store_robots,time-1,timestep,code)
        graph_end.write_image(image + "/" + code + "- Graph_End.png")
        table_end = Processing_Functions_BP.table_figure(store_robots,time-1,timestep,constants,min_neighbours,cluster_average)
        table_end.write_image(image + "/" + code + "- Table_End.png")

        Processing_Functions_BP.combine(graph_end_path,table_end_path)

        performance = Processing_Functions_BP.performance_graph(min_neighbours,np.linspace(0,len(min_neighbours),len(min_neighbours)*timestep,endpoint = False),timestep,code,"Time (s)","Minimum Average Neighbour Distance (m)")
        performance.write_image(image + "/" + code + "- Performance.png")


        #performance_intercept = Processing_Functions_BP.performance_graph(total_collision,np.linspace(0,len(total_collision),len(total_collision)*timestep,endpoint = False),timestep,code,"Time (s)","Count of Measurement Events")
        #performance_intercept.write_image(image + "/" + code + "- Intercept Performance.png")

        cluster = Processing_Functions_BP.performance_graph(cluster_average,np.linspace(0,len(cluster_average),len(cluster_average)*timestep,endpoint = False),timestep,code,"Time (s)","Average Cluster Size")
        cluster.write_image(image + "/" + code + "- Average Cluster Size.png")


        
        df = pd.DataFrame(values, columns = values_title)

        df.to_excel(path + "Tested Values.xlsx")
#performance_metric_np = np.array(performance_metric)
#np.save(current_directory + "Performance Metric.npy", performance_metric_np)
#performance_overall = Processing_Functions_BP.performance_graph(performance_metric_np[:,1],performance_metric_np[:,0],1,code,"Number of Timesteps in 1 Second ","Measurement Event Count")
#performance_overall.write_image(current_directory + "Overall Performance.png")"""

'\n#G_array = [1000,1500,2000,2500,3000,3500,4000,4500,5000,5500,6000,6500,7000,7500,8000,8500,9000,9500,10000]\n#power_array = [2,3,4,5]\n#R_array = [10,50,100,125,150,200,250]\n#multiply_array = [1,1.1,1.2,1.3,1.4,1.5,2]\nrobot_number_array =[100]#[10,20,30,40,50,60,70,80,90,100]#[10,25,50,100]\n#initial_array = [1,10,20,30,40,50,60,70,80,90,100]\nmax_force = 1\nseed_setup = 10\n\n#setting timestep parameter\ntime = 2000\ntimestep_array = 1\ntimestep = 1\nperformance_metric = []\ncurrent_directory = "Experiments/Random Seed Deployment 2/"\ntry:\n    os.mkdir(current_directory)\nexcept OSError:\n    print ("Failure: Directory creation of %s failed" % current_directory)\nelse:\n    print ("Success: Directory creation of %s succeeded" % current_directory)\n\n\nvalues = []\nrandom_generated = []\nfor i in range(seed_setup):\n    random_seed = os.urandom(8)\n    \n    random_generated.append(random_seed)\n    for robot in robot_number_array:\n        code = str(i)\n        path = (current

In [6]:
#number of robots in simulation
robot_array = [10,20,30,40,50,60,70,80,90,100]

#setting timestep parameter
time = 2000

frequency = 1
timestep = 1


initial_array = [10,20,30,40,50,60,70,80,90,100]


#initialising empty lists
performance_array = []
random_generated = []
values = []

new_path = "Experiments/Initial Deployment/"
try:
    os.mkdir(new_path)
except OSError:
    print ("Failure: Directory creation of %s failed" % new_path)
else:
    print ("Success: Directory creation of %s succeeded" % new_path)
for initial in initial_array:
    #creating an updated directory
    original_path = "Experiments/Initial Deployment/Robot Array " + str(initial) + "/"
    try:
        os.mkdir(original_path)
    except OSError:
        print ("Failure: Directory creation of %s failed" % original_path)
    else:
        print ("Success: Directory creation of %s succeeded" % original_path)
    #looping through the different random seed setups
    random_seed = os.urandom(8)
        
    performance_metric = []

    for robot in robot_array:

        #using random seed as starting point for random number generation
        random.seed(random_seed)

        #initialising performance metric list
        
        code = str(robot) + " Robots"
        #making the new path for the data
        path = (original_path + code + " /")
        try:
            os.mkdir(path)
        except OSError:
            print ("Failure: Directory creation of %s failed" % path)
        else:
            print ("Success: Directory creation of %s succeeded" % path)

        #creating the image directory
        image = (original_path + "Images/")
        try:
            os.mkdir(image)
        except OSError:
            print ("Failure: Directory creation of %s failed" % image)
        else:
            print ("Success: Directory creation of %s succeeded" % image)

        #calculating the G value used
        G_state = G_transition(max_force,R,power)

        #setting up the robot setup
        swarm = initialise(robot, side, initial,robot_speed)

        #initialising empty variables
        store_robots = np.zeros((2,robot,(time*frequency)))
        store_dust = np.zeros((2,robot,(time*frequency)))
        min_neighbours = []
        cluster_average = []
        store_dust = []
        dust_devils = []
        measurement_events = 0
        detection_metric = 0
        dust_count = 0 
        total_detection = []
        total_collision = []
        total_dust = []

        #looping through the different timesteps of the simulations
        for j in range(0,time*frequency):
            #print(j)
            #updating robots and storing robot/dust devil positions
            store_robots[:,:,j] = positions(swarm)
            store_dust.append(positions(dust_devils))

            #checking if 1 second has passed and updating velocities of the robots via the physics walk algorithm and updating status of dust devils
            if(j%frequency==0):

                dust_count = dust_count + dust(dust_devils,probability_dust,side,j,dust_speed,dust_time,timestep,frequency)
                physics_walk(swarm,G_state,power,R,max_force,multiply,1)    

            #calling update timestep method which updates positions of robots, and returns performance metrics
            measurement_events_change,detection_metric_change = update_timestep(swarm,dust_devils,timestep,frequency,min_neighbours,cluster_average,detection,R,multiply)
            measurement_events = measurement_events + measurement_events_change
            detection_metric = detection_metric + detection_metric_change

            #appending performance metrics into list for storage/post processing
            total_detection.append(detection_metric)
            total_collision.append(measurement_events)

            #updates dust devils positions
            update_dust(dust_devils)

            #storing the number of dust devils generated
            total_dust.append(dust_count)
        print(total_dust)
        print(total_detection)
        print("Total dust devils: ",len(total_dust))
        print("Total dust devils detected: ",len(total_detection))
        print(detection_metric)

        #saving robot positions
        np.save(path + "Robots.npy",store_robots)

        #saving dust devil positions
        with open( path + "dust.txt", "w") as f:
            json.dump(store_dust, f)

        #saving performance metrics - these could not be stored in excel due to storage limits
        np.save(path + "Minimum Distance to Neighbours.npy",np.array(min_neighbours))
        np.save(path + "Cluster Average.npy", np.array(cluster_average))
        np.save(path + "Measurement Events Count.npy", np.array(total_collision))
        np.save(path + "Number of Dust Devils Detected.npy", np.array(total_detection))
        np.save(path + "Number of Dust Devils Generated.npy", np.array(total_dust))
        print("Robots: ",store_robots.shape)
        print("Dust Devils: ",len(store_dust))
        print(min_neighbours)

        #adding values tested for a values excel spreadsheet for easy viewing
        values.append([len(swarm),timestep    
                    ,G_state,power,R,multiply,max_force,robot_speed,min_neighbours[time*frequency-1],cluster_average[time*frequency-1],random_seed, G_state,measurement_events,detection_metric,dust_count])

        #the titles of the variables in the values array
        values_title = ['Number of Robots',
                                        'Timestep',
                                        'G', 
                                        'Power', 
                                        'Communication Range', 
                                        'Multiplier',
                                        'Max Force',
                                        'Max Speed',
                                        'Minimum Distance to Neighbours',
                                        'Average Cluster Size',
                                        'Seed',
                                        'G Transition',
                                        'Measurement Events Count',
                                        'Number of Dust Devils Detected',
                                        'Total Number of Dust Devils',
                ]

        #storing the constants used in the simulation
        data = {'Values':[len(swarm),timestep,G_state,power,R,multiply,max_force,robot_speed,random_seed, G_state]}
        titles =['Number of Robots',
                                        'G',
                                        'Timestep', 
                                        'Power',
                                        'Communication Range', 
                                        'Multiplier',
                                        'Max Force',
                                        'Max Speed',
                                        'Seed',
                                        'G Transition',
                ]
        #setting the constants as a panda dataframe
        constants = pd.DataFrame(data, index = titles
                                       ) 

        #storing the panda dataframe
        print(constants)
        constants.to_excel(path + "Constants.xlsx")

        #setting the start paths for the graphs and the tables
        graph_start_path = image + code + "- Graph_Beginning.png"
        table_start_path = image + "/" + code + "- Table_Beginning.png"

        #using the processing functions to create plotly graphs and tables for the figures in the first timestep
        graph_start = Processing_Functions_BP.graph_figure(store_robots,0,frequency,code)
        graph_start.write_image(graph_start_path)
        table_start = Processing_Functions_BP.table_figure(store_robots,0,frequency,constants,min_neighbours,cluster_average,total_collision,total_detection,total_dust)
        table_start.write_image(table_start_path)

        #combining the tables and the graphs using pillow
        Processing_Functions_BP.combine(graph_start_path,table_start_path)

        #setting the end paths for the graphs and the tables
        graph_end_path = image + code + "- Graph_End.png"
        table_end_path = image + "/" + code + "- Table_End.png"

        #using the processing functions to create plotly graphs and tables for the figures in the last timestep
        graph_end = Processing_Functions_BP.graph_figure(store_robots,time-1,frequency,code)
        graph_end.write_image(image + "/" + code + "- Graph_End.png")
        table_end = Processing_Functions_BP.table_figure(store_robots,time-1,frequency,constants,min_neighbours,cluster_average,total_collision,total_detection,total_dust)
        table_end.write_image(image + "/" + code + "- Table_End.png")

        #combining the tables and the graphs using pillow
        Processing_Functions_BP.combine(graph_end_path,table_end_path)

        #plotting performance of the average of minimum neighbouring distance metric
        performance = Processing_Functions_BP.performance_graph(min_neighbours,np.linspace(0,len(min_neighbours),len(min_neighbours)*frequency,endpoint = False),frequency,code,"Time (s)","Minimum Average Neighbour Distance (m)")
        performance.write_image(image + "/" + code + "- Performance.png")

        #plotting performance of the dust devil measurement metric
        performance_intercept = Processing_Functions_BP.performance_graph(total_collision,np.linspace(0,len(total_collision),len(total_collision)*frequency,endpoint = False),frequency,code,"Time (s)","Count of Measurement Events")
        performance_intercept.write_image(image + "/" + code + "- Intercept Performance.png")

        #plotting performance of the cluster average of the swarm
        cluster = Processing_Functions_BP.performance_graph(cluster_average,np.linspace(0,len(cluster_average),len(cluster_average)*frequency,endpoint = False),frequency,code,"Time (s)","Average Cluster Size")
        cluster.write_image(image + "/" + code + "- Average Cluster Size.png")




        #appending the final detection performance metric to compare to other frequencies/timesteps
        performance_metric.append([robot,min_neighbours[-1]])
        
        print("Performance Metric: ", performance_metric)
        print("Total Collisions: ", total_collision)
        print(total_collision[time-1])
    #setting panda dataframe for the values tested
    df = pd.DataFrame(values, columns = values_title)

    #saving at as an excel spreadsheet
    df.to_excel(path + "Tested Values.xlsx")

    performance_metric_np = np.array(performance_metric)

    #saving performance metrics
    np.save(original_path + "Fitness.npy", performance_metric_np)

    #plotting performance of the different timesteps
    performance_overall = Processing_Functions_BP.performance_graph(performance_metric_np[:,1],performance_metric_np[:,0],1,"","Number of Robots","Number of Dust Devils Detected")
    #performance_overall.write_image(original_path + "Individual Deployment.png")

    performance_array.append(performance_metric)



Failure: Directory creation of Experiments/Initial Deployment 2/ failed
Failure: Directory creation of Experiments/Initial Deployment/Robot Array 10/ failed
Failure: Directory creation of Experiments/Initial Deployment/Robot Array 10/10 Robots / failed
Failure: Directory creation of Experiments/Initial Deployment/Robot Array 10/Images/ failed
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

Performance Metric:  [[10, 196.1967711836106]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

Performance Metric:  [[10, 196.1967711836106], [20, 197.17594552362758]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

Performance Metric:  [[10, 196.1967711836106], [20, 197.17594552362758], [30, 196.942670229186]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0

Performance Metric:  [[10, 196.1967711836106], [20, 197.17594552362758], [30, 196.942670229186], [40, 196.59961686160017]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

...

Performance Metric:  [[10, 197.22977710545405], [20, 198.80228277356895], [30, 193.97679671684043], [40, 176.8342628506389], [50, 197.00232856720106], [60, 196.91886129929966]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

Performance Metric:  [[10, 197.22977710545405], [20, 198.80228277356895], [30, 193.97679671684043], [40, 176.8342628506389], [50, 197.00232856720106], [60, 196.91886129929966], [70, 196.85235788010806]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 

Performance Metric:  [[10, 197.22977710545405], [20, 198.80228277356895], [30, 193.97679671684043], [40, 176.8342628506389], [50, 197.00232856720106], [60, 196.91886129929966], [70, 196.85235788010806], [80, 189.65085159070958]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 4, 5, 6, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7, 7

Performance Metric:  [[10, 197.22977710545405], [20, 198.80228277356895], [30, 193.97679671684043], [40, 176.8342628506389], [50, 197.00232856720106], [60, 196.91886129929966], [70, 196.85235788010806], [80, 189.65085159070958], [90, 194.96696812544118]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,

Performance Metric:  [[10, 197.22977710545405], [20, 198.80228277356895], [30, 193.97679671684043], [40, 176.8342628506389], [50, 197.00232856720106], [60, 196.91886129929966], [70, 196.85235788010806], [80, 189.65085159070958], [90, 194.96696812544118], [100, 192.84007804008874]]
Total Collisions:  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [13]:
np.save(original_path + "Average Minimum Neighbour Distance for Different Deployments.npy",performance_array)

In [26]:

labels = []
for initial in (initial_array):
    labels.append("Between " + str(-initial) + " and " + str(initial))
initial = 100
labels.append("Between " + str(-initial) + " and " + str(initial))
print(labels)
data = []
for i in range(len(performance_array)):
    values = performance_array[i]
    print(values)
    np_array = np.array(values)
    print(np_array)
    print("First" + str(np_array[:,0]))
    data.append(go.Scatter(
    x=np_array[:,0],
    y=np_array[:,1],
    name = labels[i],
    line=dict( dash='dot')))
layout = go.Layout(title="<b>Average Minimum Neighbour Distance (m) versus Number of Robots for Different Deployments</b>",
    xaxis_title="Number of Robots",
    yaxis_title="Average Minimum Neighbour Distance (m)",
         title_font=dict(
        size=12
    ),    )
print(data)
fig = go.Figure(data=data, layout=layout)
fig.write_image(new_path + "Comparing Deployments 2.png")

['Between -10 and 10', 'Between -20 and 20', 'Between -30 and 30', 'Between -40 and 40', 'Between -50 and 50', 'Between -60 and 60', 'Between -70 and 70', 'Between -80 and 80', 'Between -90 and 90', 'Between -100 and 100', 'Between -100 and 100']
[[10, 157.37777449763104], [20, 176.30499535446725], [30, 164.51188697351188], [40, 178.89401025537217], [50, 182.37126903589905], [60, 169.4470035212077], [70, 170.3299373580108], [80, 159.86137328171782], [90, 117.66222981639112], [100, 146.63583413911536]]
[[ 10.         157.3777745 ]
 [ 20.         176.30499535]
 [ 30.         164.51188697]
 [ 40.         178.89401026]
 [ 50.         182.37126904]
 [ 60.         169.44700352]
 [ 70.         170.32993736]
 [ 80.         159.86137328]
 [ 90.         117.66222982]
 [100.         146.63583414]]
First[ 10.  20.  30.  40.  50.  60.  70.  80.  90. 100.]
[[10, 197.39515149523905], [20, 197.38922700467208], [30, 184.8164548129893], [40, 197.7063942492801], [50, 180.53744660212777], [60, 182.0564104